In [1]:
#Data Pre-processing part
import os
import random
import pandas as pd

In [2]:
# from datasets import load_dataset

# dataset = load_dataset("google/fleurs",'hi_in')

In [3]:
train_path = "/hdd/Gothi_raj/Whisper/dataset/kathbath/kb_data_clean_wav/hindi/train/bucket.csv"

audio = []
transcript= []

flg=0
with open(train_path,'r') as f:
    lines = f.readlines()
    for line in lines:
        # print(line)
        if flg==0:        
            flg=1
            continue
        line = line.split(',')
        audio.append(line[0])
        transcript.append(line[1])

In [4]:
train_df = pd.DataFrame({'path':audio,'transcription':transcript})

In [5]:
dev_path = "/hdd/Gothi_raj/Whisper/dataset/kathbath/kb_data_clean_wav/hindi/valid/bucket.csv"

audio = []
transcript= []

flg=0
with open(dev_path,'r') as f:
    lines = f.readlines()
    for line in lines:
        # print(line)
        if flg==0:        
            flg=1
            continue
        line = line.split(',')
        audio.append(line[0])
        transcript.append(line[1])

In [6]:
dev_df = pd.DataFrame({'path':audio,'transcription':transcript})

In [7]:
from datasets import DatasetDict,Dataset

train_data_hf = Dataset.from_pandas(train_df)
dev_data_hf = Dataset.from_pandas(dev_df)

dataset = DatasetDict({'train':train_data_hf,'validation':dev_data_hf})
dataset

/hdd/Gothi_raj/envs/wt/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


DatasetDict({
    train: Dataset({
        features: ['path', 'transcription'],
        num_rows: 93024
    })
    validation: Dataset({
        features: ['path', 'transcription'],
        num_rows: 3229
    })
})

In [8]:
import re
chars_to_ignore_regex = '[\,\?\.\!\-\;\:\"]'
from whisper.normalizers import IndicTextNormalizer

normalizer = IndicTextNormalizer(use_indic_normalizer = True, lang = 'hindi')

def remove_special_characters(batch):
    # batch["transcription"] = re.sub(chars_to_ignore_regex, '', batch["transcription"]).lower()
    batch["transcription"] = normalizer(batch["transcription"])
    return batch
dataset = dataset.map(remove_special_characters)

In [9]:
import os
import sys
current_directory = os.getcwd()
sys.path.append(current_directory)

In [10]:
current_directory

'/hdd/Gothi_raj/Whisper'

In [11]:
# %cd ..

In [12]:
from transformers import WhisperFeatureExtractor

model_path = "openai/whisper-large-v3"

feature_extractor = WhisperFeatureExtractor.from_pretrained(model_path,cache_dir='/hdd/Gothi_raj/HF_model')

In [13]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained(model_path, language="hindi", task="transcribe",cache_dir='/hdd/Gothi_raj/HF_model')

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [14]:
# tokenizer.add_tokens(decoded_tokens)

In [15]:
# print(len(tokenizer.get_vocab()))

In [16]:
input_str = dataset["train"][0]["transcription"]

# tokenizer.add_tokens("IndoAryan")

prompt = "indoaryan"
prompt_ids = tokenizer.get_prompt_ids(prompt)
print(prompt_ids)

labels = tokenizer(input_str).input_ids
print(labels)

new_list = []
new_list.extend(prompt_ids)
new_list.extend(labels)
print(new_list)

# tokenizer = WhisperTokenizer.from_pretrained(model_path, language="Bengali", task="transcribe")
# tokenizer.add_tokens(decoded_tokens)
# labels = [51, 71, 72, 82, 53552, 82, 53869, 340, 2455, 83, 50257]

decoded_with_special = tokenizer.decode(labels, skip_special_tokens=False)
decode_with_prompt = tokenizer.decode(new_list, skip_special_tokens=False)
decoded_str = tokenizer.decode(labels, skip_special_tokens=True)

print(f"Input:                 {input_str}")
print(f"Decoded w/ special:    {decoded_with_special}")
print(f"Decoded w/ prompt special:{decode_with_prompt}")
print(f"Decoded w/out special: {decoded_str}")
print(f"Are equal:             {input_str == decoded_str}")

[50362 13770   822   282]
[50258, 50276, 50360, 50364, 44500, 17937, 46758, 17937, 31945, 41858, 33279, 8485, 248, 33279, 41858, 33279, 36158, 27099, 45938, 41858, 33926, 31945, 8485, 101, 21981, 8485, 250, 21981, 45938, 31881, 3941, 241, 31970, 31881, 48449, 8703, 234, 36158, 37139, 17937, 25411, 27099, 3941, 253, 8485, 227, 3941, 253, 43372, 41858, 49316, 21981, 37139, 8703, 223, 3941, 230, 8485, 105, 36158, 17937, 48268, 17937, 37139, 43372, 50257]
[50362, 13770, 822, 282, 50258, 50276, 50360, 50364, 44500, 17937, 46758, 17937, 31945, 41858, 33279, 8485, 248, 33279, 41858, 33279, 36158, 27099, 45938, 41858, 33926, 31945, 8485, 101, 21981, 8485, 250, 21981, 45938, 31881, 3941, 241, 31970, 31881, 48449, 8703, 234, 36158, 37139, 17937, 25411, 27099, 3941, 253, 8485, 227, 3941, 253, 43372, 41858, 49316, 21981, 37139, 8703, 223, 3941, 230, 8485, 105, 36158, 17937, 48268, 17937, 37139, 43372, 50257]
Input:                 हालांकि चिकित्सकों ने जेसीओ की मौत हार्ट अटैक से हुई बताया है
Decod

In [17]:
prompt = "indo"
prompt_ids = tokenizer.get_prompt_ids(prompt)
print(prompt_ids)

[50362 13770]


In [4]:
prompt = "dra"
prompt_ids = tokenizer.get_prompt_ids(prompt)
print(prompt_ids)

[50361  1617]


In [18]:
# tokenizer.encode('IndoAryan')

[50258, 50333, 50359, 50363, 51865, 50257]

In [27]:
# tokenizer.decode([13770 ,822 ,282])

print(tokenizer.decode([13770 ]))
print(tokenizer.decode([13770 ,822]))
tokenizer.decode([13770 ,822,282])

 indo
 indoary


' indoaryan'

In [30]:
# tokenizer.decode([13770 ,822 ,282])

print(tokenizer.decode([1617 ]))
print(tokenizer.decode([1617, 6833]))
tokenizer.decode([1617  , 6833 , 952])

 dra
 dravid


' dravidian'

In [20]:
tokenizer.decode([51865])

'IndoAryan'

In [12]:
dataset['train'][0]

{'path': '/raid/speech/rajgothi/whisper/kathbath/kb_data_clean_wav/gujarati/train/audio/107/844424931458674-107-f.wav',
 'transcription': 'વ્યવસાયોના બહુવિધ રેખાઓ ધરાવતા વ્યવસાયો માટે આવકને ફાળવવામાં આવવી જોઈએ'}

In [98]:
# train_path = dataset['train']['path']
# new_path = []
# for path in train_path:
#     path = path.split('/')
#     path = '/'.join(path[:-1]) + '/train/' + path[-1]
#     new_path.append(path)

# dataset['train'] = dataset['train'].remove_columns(['path'])
# dataset['train'] = dataset['train'].add_column("path", new_path)

# dev_path = dataset['validation']['path']
# new_path = []
# for path in dev_path:
#     path = path.split('/')
#     path = '/'.join(path[:-1]) + '/dev/' + path[-1]
#     new_path.append(path)

# dataset['validation'] = dataset['validation'].remove_columns(['path'])
# dataset['validation'] = dataset['validation'].add_column("path", new_path)


# test_path = dataset['test']['path']
# new_path = []
# for path in test_path:
#     path = path.split('/')
#     path = '/'.join(path[:-1]) + '/test/' + path[-1]
#     new_path.append(path)

# dataset['test'] = dataset['test'].remove_columns(['path'])
# dataset['test'] = dataset['test'].add_column("path", new_path)

In [18]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained(model_path, language="hindi", task="transcribe")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [19]:
from datasets import Audio

dataset = dataset.cast_column("path", Audio(sampling_rate=16000))
dataset

DatasetDict({
    train: Dataset({
        features: ['path', 'transcription'],
        num_rows: 93024
    })
    validation: Dataset({
        features: ['path', 'transcription'],
        num_rows: 3229
    })
})

In [20]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["path"]

    # compute log-Mel input features from input audio array 
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids 
    batch["labels"] = tokenizer(batch["transcription"]).input_ids
    return batch

In [21]:
new_dataset = []
new_dataset.append(dataset['train'].select(range(40000)))
new_dataset.append(dataset['train'].select(range(40000,80000)))
new_dataset.append(dataset['train'].select(range(80000,93024)))
new_dataset

[Dataset({
     features: ['path', 'transcription'],
     num_rows: 40000
 }),
 Dataset({
     features: ['path', 'transcription'],
     num_rows: 40000
 }),
 Dataset({
     features: ['path', 'transcription'],
     num_rows: 13024
 })]

In [17]:
# new_dataset[0]['path']

Exception ignored from cffi callback <function SoundFile._init_virtual_io.<locals>.vio_read at 0x7a99b15829e0>:
Traceback (most recent call last):
  File "/hdd/Gothi_raj/envs/wt/lib/python3.10/site-packages/soundfile.py", line 1245, in vio_read
    buf = _ffi.buffer(ptr, count)
KeyboardInterrupt: 


In [22]:
processed = []
for i in range(len(new_dataset)):
    processed.append(new_dataset[i].map(prepare_dataset, remove_columns=new_dataset[i].column_names, num_proc=1))

Map:  30%|██▉       | 11989/40000 [01:47<01:53, 245.86 examples/s] 

: 

In [ ]:
from datasets import concatenate_datasets
dataset['train']  = concatenate_datasets(processed)

In [ ]:
dataset['validation'] = dataset['validation'].map(prepare_dataset, remove_columns=dataset.column_names['validation'], num_proc=1)

In [17]:
dataset

DatasetDict({
    train: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 71063
    })
    validation: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 3139
    })
})

In [36]:
dataset['validation'][0]

{'input_features': [[-0.7874431610107422,
   -0.7874431610107422,
   -0.7874431610107422,
   -0.7874431610107422,
   0.5345555543899536,
   0.667984127998352,
   -0.2815629243850708,
   -0.20383727550506592,
   -0.21127736568450928,
   -0.29339444637298584,
   -0.3674379587173462,
   -0.12926483154296875,
   -0.21462929248809814,
   -0.4487617015838623,
   -0.32083189487457275,
   -0.3362194299697876,
   -0.2798973321914673,
   -0.32740044593811035,
   -0.5225925445556641,
   -0.32707250118255615,
   -0.39623916149139404,
   -0.2674674987792969,
   -0.3607727289199829,
   -0.3601294755935669,
   -0.3356412649154663,
   -0.33303964138031006,
   -0.19379985332489014,
   -0.17310857772827148,
   -0.32270002365112305,
   -0.47878122329711914,
   -0.3937767744064331,
   -0.3134615421295166,
   -0.24414503574371338,
   -0.1350177526473999,
   -0.2821156978607178,
   -0.32568061351776123,
   -0.04245173931121826,
   -0.05724954605102539,
   -0.250362753868103,
   -0.20533013343811035,
   -0.1

In [ ]:
save_path = '/hdd2/raj/preprocess/hindi_kathbath_largev3'

dataset.save_to_disk(save_path)

# dataset.save_to_disk('Dataset/gujarati_kathbath_original')

Saving the dataset (0/137 shards):   0%|          | 0/71063 [00:00<?, ? examples/s]

Saving the dataset (0/7 shards):   0%|          | 0/3139 [00:00<?, ? examples/s]

In [38]:
dataset

DatasetDict({
    train: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 93024
    })
    validation: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 3229
    })
})

In [8]:
from datasets import load_from_disk

dataset = load_from_disk("Dataset/gujarati_kathbath_original")

In [9]:
dataset

DatasetDict({
    train: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 71063
    })
    validation: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 3139
    })
})

In [10]:
for ind,label in enumerate(dataset['train']['labels']):
    if len(label)>448:
        # print(len(label))
        print(ind)

27276
65880
70793


In [11]:

# what we don't want
exclude_idx = [27276,65880,70793]

# create new dataset exluding those idx
dataset['train'] = dataset['train'].select(
    (
        i for i in range(len(dataset['train'])) 
        if i not in set(exclude_idx)
    )
)

In [16]:
dataset

DatasetDict({
    train: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 71060
    })
    validation: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 3139
    })
})

In [15]:
for ind,label in enumerate(dataset['validation']['labels']):
    if len(label)>448:
        # print(len(label))
        print(ind)

In [21]:
dataset.save_to_disk('Dataset/gujarati_kathbath_original_new')

Saving the dataset (0/137 shards):   0%|          | 0/71060 [00:00<?, ? examples/s]

Saving the dataset (0/7 shards):   0%|          | 0/3139 [00:00<?, ? examples/s]